In [42]:
import sys
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse

In [10]:
df

gene_name   GMCSF_005   GMCSF_008     IL3_005     IL3_008  \
0           TSPAN6    0.000000    0.000000    0.000000    0.000000   
1             TNMD    0.000000    0.000000    0.000000    0.000000   
2             DPM1  207.775307  183.415566  180.411727  152.199347   
3            SCYL3   11.288142   16.418016   13.478499   13.081465   
4         C1orf112    6.740225    6.599070    6.029320    3.771663   
...            ...         ...         ...         ...         ...   
63920   AL591163.1    0.000000    0.469565    0.000000    0.000000   
63921   AL589702.1    0.000000    0.000000    0.000000    0.000000   
63922  AC068587.10    0.000000    0.000000    0.000000    0.000000   
63923   AL034417.4    0.498066    0.788199    1.838902    0.294413   
63924   AL513220.1    0.000000    0.000000    0.000000    0.000000   

          IL5_005     IL5_008  neg_control_005  neg_control_008  \
0        0.000000    0.232101         0.000000         0.080366   
1        0.000000    0.000000         0.000000         0.000000   
2      217.833559  235.071182       164.469210       155.262732   
3       18.788914   14.119486        12.320239        10.304713   
4        6.601151    4.117646         5.999837         4.692484   
...           ...         ...              ...              ...   
63920    0.000000    0.000000         0.636346         0.000000   
63921    0.000000    0.000000         0.000000         0.000000   
63922    0.000000    0.000000         0.000000         0.000000   
63923    1.032261    1.014368         1.679380         0.361647   
63924    0.403158    0.000000         0.000000         0.000000   

       09_007_NegCtrl  ...  19_002_IL5  20_002_GMCSF  21_018_NegCtrl  \
0            0.681828  ...    0.000000      0.000000        0.148158   
1            0.000000  ...    0.000000      0.000000        0.000000   
2          124.841643  ...  179.438339    128.304778      141.099160   
3           12.164428  ...   14.721884     18.872070       13.656976   
4            4.364731  ...    9.100162      8.268718        9.587928   
...               ...  ...         ...           ...             ...   
63920        0.000000  ...    0.672599      0.000000        0.000000   
63921        0.000000  ...    0.000000      0.000000        0.000000   
63922        0.000000  ...    0.000000      0.000000        0.000000   
63923        1.203529  ...    0.642483      1.517776        2.645675   
63924        0.000000  ...    0.000000      0.000000        0.000000   

       22_018_IL3  23_018_IL5  24_018_GMCSF  25_019_NegCtrl  26_019_IL3  \
0        0.000000    0.154622      0.115682        0.191136    0.201222   
1        0.000000    0.000000      0.000000        0.000000    0.000000   
2      176.813766   93.265636    181.808903      145.861966  160.377942   
3       11.047178   13.102774     10.908363       10.804218    8.912448   
4        5.508859    9.254407      7.476470        4.919239    5.332377   
...           ...         ...           ...             ...         ...   
63920    0.000000    2.124619      0.000000        0.000000    0.000000   
63921    0.000000    0.000000      0.000000        0.000000    0.000000   
63922    0.000000    0.000000      0.000000        0.000000    0.000000   
63923    0.239882    2.038718      1.915176        1.906331    1.433705   
63924    0.000000    0.000000      0.000000        0.000000    0.000000   

       27_019_IL5  28_019_GMCSF  
0        0.223939      0.000000  
1        0.000000      0.000000  
2      189.388777    189.377154  
3       14.371017      9.285853  
4       10.656557      8.475995  
...           ...           ...  
63920    0.000000      0.000000  
63921    0.000000      0.000000  
63922    0.000000      0.000000  
63923    0.856809      1.619717  
63924    0.000000      0.000000  

[63925 rows x 29 columns]

In [43]:
# Read TPM counts
df = pd.DataFrame(pd.read_csv('GSE128027_Nelson_TPM.txt', sep = '\t', header=0))
# Read ih file
ih_df = pd.DataFrame(pd.read_csv('GSE128027-GPL16791-ih.txt', sep = '\t', header=0))
# This is so we can easily rename expr columns to GSM IDs using information in the ih file.
gsm_dict = {ih_df["ClinicalHeader"][i]:ih_df["ArrayID"][i] for i in ih_df.index}
df = df.rename(columns=gsm_dict)

expr = df.copy(deep=True)
expr = expr.drop(['gene_name'], axis=1)

print("Taking log")
adata = sc.AnnData(expr.T)
sc.pp.log1p(adata, base = 2)

expr = pd.DataFrame(adata.X)
expr = expr.T
expr.columns = df.columns[1:]

genes = pd.DataFrame()
genes["ProbeID"] = df["gene_name"]
genes["Name"] = df["gene_name"]
expr = pd.concat([genes, expr], axis=1)

Taking log


/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


In [44]:
expr

ProbeID         Name  GSM3660549  GSM3660550  GSM3660551  \
0           TSPAN6       TSPAN6    0.000000    0.000000    0.000000   
1             TNMD         TNMD    0.000000    0.000000    0.000000   
2             DPM1         DPM1    7.705807    7.526816    7.503124   
3            SCYL3        SCYL3    3.619195    4.122509    3.855840   
4         C1orf112     C1orf112    2.952376    2.925823    2.813385   
...            ...          ...         ...         ...         ...   
63920   AL591163.1   AL591163.1    0.000000    0.555389    0.000000   
63921   AL589702.1   AL589702.1    0.000000    0.000000    0.000000   
63922  AC068587.10  AC068587.10    0.000000    0.000000    0.000000   
63923   AL034417.4   AL034417.4    0.583102    0.838507    1.505333   
63924   AL513220.1   AL513220.1    0.000000    0.000000    0.000000   

       GSM3660552  GSM3660553  GSM3660554  GSM3660555  GSM3660556  ...  \
0        0.000000    0.000000    0.301121    0.000000    0.111520  ...   
1        0.000000    0.000000    0.000000    0.000000    0.000000  ...   
2        7.259266    7.773690    7.883078    7.370419    7.287830  ...   
3        3.815726    4.306621    3.918337    3.735548    3.498852  ...   
4        2.254492    2.926218    2.355480    2.807321    2.509058  ...   
...           ...         ...         ...         ...         ...  ...   
63920    0.000000    0.000000    0.000000    0.710478    0.000000  ...   
63921    0.000000    0.000000    0.000000    0.000000    0.000000  ...   
63922    0.000000    0.000000    0.000000    0.000000    0.000000  ...   
63923    0.372297    1.023085    1.010327    1.421899    0.445353  ...   
63924    0.000000    0.488677    0.000000    0.000000    0.000000  ...   

       GSM3660567  GSM3660568  GSM3660569  GSM3660570  GSM3660571  GSM3660572  \
0        0.000000    0.000000    0.199321    0.000000    0.207420    0.157926   
1        0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
2        7.495362    7.014632    7.150754    7.474223    6.558660    7.514193   
3        3.974702    4.312670    3.873516    3.590624    3.817907    3.573903   
4        3.336307    3.212370    3.404348    2.702405    3.358172    3.083463   
...           ...         ...         ...         ...         ...         ...   
63920    0.742092    0.000000    0.000000    0.000000    1.643680    0.000000   
63921    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
63922    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
63923    0.715878    1.332150    1.866186    0.310202    1.603463    1.543583   
63924    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   

       GSM3660573  GSM3660574  GSM3660575  GSM3660576  
0        0.252338    0.264503    0.291531    0.000000  
1        0.000000    0.000000    0.000000    0.000000  
2        7.198318    7.334300    7.572805    7.572717  
3        3.561230    3.309241    3.942141    3.362590  
4        2.565412    2.662747    3.543070    3.244277  
...           ...         ...         ...         ...  
63920    0.000000    0.000000    0.000000    0.000000  
63921    0.000000    0.000000    0.000000    0.000000  
63922    0.000000    0.000000    0.000000    0.000000  
63923    1.539199    1.283154    0.892825    1.389411  
63924    0.000000    0.000000    0.000000    0.000000  

[63925 rows x 30 columns]

In [45]:
path_dir = "./"
expr.to_csv(path_dir+"GSE128027-GPL16791-expr.txt", header=True, index=False,sep='\t')

In [46]:
# Build idx file

def make_idx():
    print('Starting make_idx')
    expr = path_dir+'GSE128027-GPL16791-expr.txt'

    ptr = []
    ids = []
    name = []
    desc = []
    pos = 0

    with open(expr, 'rb') as f:
        for line in f:
            if pos == 0:
                pos += len(line)
            else:
                ptr.append(pos)
                pos += len(line)
                split = line.decode("utf-8").split('\t')
                ids.append(split[0])
                name.append(split[1].split(':')[0])
                desc.append(':'.join(split[1].split(':')[1:]))
        f.close()

    with open(path_dir+'GSE128027-GPL16791-idx.txt', 'w') as f:
        f.write('ProbeID\tPtr\tName\tDescription\n')
        for i in range(len(ids)):
            f.write('{}\t{}\t{}\t{}\n'.format(ids[i], ptr[i], name[i], desc[i]))
        f.close()
    print("Done with make_idx")
    
make_idx()

Starting make_idx
Done with make_idx
